# 1. Using Memory

This notebook looks at including memory operations in our machine code programs.

First, some hints from the last homework.

## 1.1 Weird Memory

You can use `%dump START STOP` to look at contiguous memory locations.

In [9]:
%dump x3000 x300A

Memory dump:
           x3000: xE002
           x3001: x6201
           x3002: xF025
           x3003: xF0F0
           x3004: x000F
           x3005: x0000
           x3006: x0000
           x3007: x0000
           x3008: x0000
           x3009: x0000
           x300A: x0000


If you find that you have weird things in memory, you can perform a `%reset` of the LC3:

In [10]:
%reset


Welcome to the LC-3 simulator.

The contents of the LC-3 tools distribution, including sources, management
tools, and data, are Copyright (c) 2003 Steven S. Lumetta.

The LC-3 tools distribution is free software covered by the GNU General
Public License, and you are welcome to modify it and/or distribute copies
of it under certain conditions.  The file COPYING (distributed with the
tools) specifies those conditions.  There is absolutely no warranty for
the LC-3 tools distribution, as described in the file NO_WARRANTY (also
distributed with the tools).

Have fun.

Registers:
PC: x3000
N: 0 Z: 1 P: 0 
R0: x0000 R1: x0000 R2: x0000 R3: x0000 
R4: x0000 R5: x0000 R6: x0000 R7: x0000 


In [11]:
%dump x3000 x300A

Memory dump:
           x3000: x0000
           x3001: x0000
           x3002: x0000
           x3003: x0000
           x3004: x0000
           x3005: x0000
           x3006: x0000
           x3007: x0000
           x3008: x0000
           x3009: x0000
           x300A: x0000


That looks better!

## 1.2 Infinite Loops

If you find yourself running an infinite loop, like this:

In [12]:
.ORIG x3000
0000 111 111111111   ; BRnzp go -1
.END

Memory dump:
           x3000: x0FFF

Registers:
PC: x3001
N: 0 Z: 1 P: 0 
R0: x0000 R1: x0000 R2: x0000 R3: x0000 
R4: x0000 R5: x0000 R6: x0000 R7: x0000 


In [13]:
%exe

Keyboard Interrupt!


Press the black square in the toolbar, or select menu -> Kernel -> Interrupt. That should send a `Keyboard Interrupt` to the LC3 and stop it from running.

## 1.3 Clear

There is no CLR instruction. You can use something like:

```gas
0101 001 001 1 00000 ;; AND R0, R0, #0
```

## 1.4 Using BR

Using a BR instruction is the only way to have any program control at all. There is no IF, FOR, WHILE, etc. You have to use BR to build such constructs.

In [3]:
.ORIG x3000
0101 000 000 1 00000 ; R0 to 0
0001 000 000 1 01010 ; R0 <- R0 
0000 010 000000011   ; BRp go to +3
0001 001 000 0 00 000 ; R1 <- R0 
0001 000 000 1 11111 ; R0 - 1
0000 111 111111100   ; BR go to -4
1111 0000 00100101   ; HALT
.END

Memory dump:
           x3000: x1020
           x3001: x102A
           x3002: x0403
           x3003: x1220
           x3004: x103F
           x3005: x0FFC
           x3006: xF025
           x3007: x0000
           x3008: x0000
           x3009: x0000
           x300A: x0000

Registers:
PC: x3007
N: 0 Z: 1 P: 0 
R0: x0000 R1: x0000 R2: x0000 R3: x0000 
R4: x0000 R5: x0000 R6: x0000 R7: x0000 


In [4]:
%exe

Computation completed
Instructions: 44
Cycles: 267 (0.000133 milliseconds)

Registers:
PC: x048E
N: 0 Z: 1 P: 0 
R0: x0000 R1: x0001 R2: x0000 R3: x0000 
R4: x0000 R5: x0000 R6: x0000 R7: x3007 


## 1.5 Don't use a calculator, use your programming languages!

In [1]:
%%python

print(bin(16 * 15 + 15))
print(hex(16 * 15 + 15))


0b11111111
0xff


## 1.6 Loading Memory

You can stick data into memory using the .ORIG directive:

In [4]:
.ORIG x3001
1111111111111111
.END

Memory dump:
           x3001: xFFFF
           x3002: x0000

Registers:
PC: x3002
N: 0 Z: 1 P: 0 
R0: x0000 R1: x0000 R2: x0000 R3: x0000 
R4: x0000 R5: x0000 R6: x0000 R7: x0000 


In [5]:
.ORIG x3000
1111111111111110
.END

Memory dump:
           x3000: xFFFE
           x3001: xFFFF
           x3002: x0000

Registers:
PC: x3001
N: 0 Z: 1 P: 0 
R0: x0000 R1: x0000 R2: x0000 R3: x0000 
R4: x0000 R5: x0000 R6: x0000 R7: x0000 


In [8]:
%%html

<style>
table {float: left}
</style>

## 1.7 Loading from Memory

### 1.7.1 LD - Load

```gas
LD R4, VALUE   ; R4 <- mem[VALUE]
```

15 - 12 | 11 - 9 | 8 - 0 |
----| ------ | ----
0010 | DR | PCoffset9

<br clear="all"/>

* DR <- mem[ PC<sup>+</sup> + SEXT(PCoffset9) ]
* sets condition codes

### 1.7.2 LDI - Load Indirect

```gas
LDI R4, VALUE   ; R4 <- mem[mem[VALUE]]
```

15 - 12 | 11 - 9 | 8 - 0 |
----| ------ | ----
1010 | DR | PCoffset9

<br clear="all"/>

* DR <- mem[mem[ PC<sup>+</sup> + SEXT(PCoffset9) ]]
* sets condition codes

### 1.7.3 LDR - Load Base + Offset

```gas
LDR R4, R1, VALUE   ; R4 <- mem[R1 + VALUE]
```

15 - 12 | 11 - 9 | 8 - 6 | 5 - 0 |
----| ------ | ----
0110 | DR | BaseR | offset6

<br clear="all"/>

* DR <- mem[ BaseR + SEXT(offset6) ]
* sets condition codes

### 1.7.4 LEA - Load Effective Address

```gas
LEA R4, VALUE   ; R4 <- address of VALUE
```

15 - 12 | 11 - 9 | 8 - 0 |
----| ------ | ----
1110 | DR | PCoffset9

<br clear="all"/>

* DR <- PC<sup>+</sup> + SEXT(PCoffset9) 
* sets condition codes

## Example

### Example of LD

In [14]:
%reset


Welcome to the LC-3 simulator.

The contents of the LC-3 tools distribution, including sources, management
tools, and data, are Copyright (c) 2003 Steven S. Lumetta.

The LC-3 tools distribution is free software covered by the GNU General
Public License, and you are welcome to modify it and/or distribute copies
of it under certain conditions.  The file COPYING (distributed with the
tools) specifies those conditions.  There is absolutely no warranty for
the LC-3 tools distribution, as described in the file NO_WARRANTY (also
distributed with the tools).

Have fun.

Registers:
PC: x3000
N: 0 Z: 1 P: 0 
R0: x0000 R1: x0000 R2: x0000 R3: x0000 
R4: x0000 R5: x0000 R6: x0000 R7: x0000 


In [18]:
.ORIG x3000
0010 000 000000001 ;; load next next into R0
1111 0000 00100101 ;; HALT
1111 0000 1111 0000
.END

Memory dump:
           x3000: x2001
           x3001: xF025
           x3002: xF0F0
           x3003: x0000
           x3004: x0000
           x3005: x0000
           x3006: x0000
           x3007: x0000
           x3008: x0000
           x3009: x0000
           x300A: x0000
           x300B: x0000
           x300C: x0000
           x300D: x0000
           x300E: x0000
           x300F: x0000
           x3010: x0000
           x3011: x0000
           x3012: x0000
           x3013: x0000
           x3014: x0000
           x3015: x0000
           x3016: x0000
           x3017: x0000
           x3018: x0000
           x3019: x0000
           x301A: x0000
           x301B: x0000
           x301C: x0000
           x301D: x0000
           x301E: x0000
           x301F: x0000
           x3020: x0000
           x3021: x0000
           x3022: x0000
           x3023: x0000
           x3024: x0000
           x3025: x0000
           x3026: x0000
           x3027: x0000
           x3028: x0000
   

In [19]:
%exe

Computation completed
Instructions: 2
Cycles: 19 (0.000010 milliseconds)

Registers:
PC: x048E
N: 1 Z: 0 P: 0 
R0: xF0F0 R1: x0000 R2: x0000 R3: x0000 
R4: x0000 R5: x0000 R6: x0000 R7: x3002 


### Example of LDI

In [17]:
.ORIG xF0F0
1111 1110 1110 1101
.END

Memory dump:
           xF0F0: xFEED

Registers:
PC: xF0F1
N: 0 Z: 1 P: 0 
R0: x0000 R1: x0000 R2: x0000 R3: x0000 
R4: x0000 R5: x0000 R6: x0000 R7: x0000 


In [20]:
.ORIG x3000
1010 000 000000001 ;; R0 <- mem[mem[]]
1111 0000 00100101 ;; HALT
1111 0000 1111 0000
.END

Memory dump:
           x3000: xA001
           x3001: xF025
           x3002: xF0F0
           x3003: x0000
           x3004: x0000
           x3005: x0000
           x3006: x0000
           x3007: x0000
           x3008: x0000
           x3009: x0000
           x300A: x0000
           x300B: x0000
           x300C: x0000
           x300D: x0000
           x300E: x0000
           x300F: x0000
           x3010: x0000
           x3011: x0000
           x3012: x0000
           x3013: x0000
           x3014: x0000
           x3015: x0000
           x3016: x0000
           x3017: x0000
           x3018: x0000
           x3019: x0000
           x301A: x0000
           x301B: x0000
           x301C: x0000
           x301D: x0000
           x301E: x0000
           x301F: x0000
           x3020: x0000
           x3021: x0000
           x3022: x0000
           x3023: x0000
           x3024: x0000
           x3025: x0000
           x3026: x0000
           x3027: x0000
           x3028: x0000
   

In [21]:
%exe

Computation completed
Instructions: 2
Cycles: 21 (0.000010 milliseconds)

Registers:
PC: x048E
N: 1 Z: 0 P: 0 
R0: xFEED R1: x0000 R2: x0000 R3: x0000 
R4: x0000 R5: x0000 R6: x0000 R7: x3002 


### Example of LDR and LEA

In [22]:
.ORIG x3000
1110 000 000000010  ;; LEA R0 <- address of [PC+ + 2]
0110 001 000 000001 ;; LDR R1 <- mem[r0 + 1]
1111 0000 00100101  ;; HALT
1111 0000 1111 0000
0000 0000 0000 1111 
.END

Memory dump:
           x3000: xE002
           x3001: x6201
           x3002: xF025
           x3003: xF0F0
           x3004: x000F
           x3005: x0000
           x3006: x0000
           x3007: x0000
           x3008: x0000
           x3009: x0000
           x300A: x0000
           x300B: x0000
           x300C: x0000
           x300D: x0000
           x300E: x0000
           x300F: x0000
           x3010: x0000
           x3011: x0000
           x3012: x0000
           x3013: x0000
           x3014: x0000
           x3015: x0000
           x3016: x0000
           x3017: x0000
           x3018: x0000
           x3019: x0000
           x301A: x0000
           x301B: x0000
           x301C: x0000
           x301D: x0000
           x301E: x0000
           x301F: x0000
           x3020: x0000
           x3021: x0000
           x3022: x0000
           x3023: x0000
           x3024: x0000
           x3025: x0000
           x3026: x0000
           x3027: x0000
           x3028: x0000
   

In [23]:
%exe

Computation completed
Instructions: 3
Cycles: 24 (0.000012 milliseconds)

Registers:
PC: x048E
N: 0 Z: 0 P: 1 
R0: x3003 R1: x000F R2: x0000 R3: x0000 
R4: x0000 R5: x0000 R6: x0000 R7: x3003 


In [8]:
.ORIG x3100
0000 0000 0000 0001
0000 0000 0000 0001
0000 0000 0000 0001
0000 0000 0000 0001
0000 0000 0000 0001
0000 0000 0000 0001
0000 0000 0000 0001
0000 0000 0000 0001
0000 0000 0000 0001
0000 0000 0000 0001
.END

Memory dump:
           x3100: x0001
           x3101: x0001
           x3102: x0001
           x3103: x0001
           x3104: x0001
           x3105: x0001
           x3106: x0001
           x3107: x0001
           x3108: x0001
           x3109: x0001
           x310A: x0000
           x310B: x0000
           x310C: x0000
           x310D: x0000
           x310E: x0000
           x310F: x0000
           x3110: x0000
           x3111: x0000
           x3112: x0000
           x3113: x0000
           x3114: x0000
           x3115: x0000
           x3116: x0000
           x3117: x0000
           x3118: x0000
           x3119: x0000
           x311A: x0000
           x311B: x0000
           x311C: x0000
           x311D: x0000
           x311E: x0000
           x311F: x0000
           x3120: x0000
           x3121: x0000
           x3122: x0000
           x3123: x0000
           x3124: x0000
           x3125: x0000
           x3126: x0000
           x3127: x0000
           x3128: x0000
   